In [18]:
from PIL import Image
import glob
import re
from random import *
from os import listdir
from pickle import dump
from keras.applications.vgg19 import VGG19
from keras.preprocessing.image import load_img
from keras.preprocessing.image import img_to_array
from keras.applications.vgg19 import preprocess_input
from keras.models import Model
from pickle import load
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from keras.utils import plot_model
from keras.models import Model
from keras.layers import Input
from keras.layers import Dense
from keras.layers import LSTM
from keras.layers import Embedding
from keras.layers import Dropout
from keras.layers.merge import add
from keras.callbacks import ModelCheckpoint
import numpy as np
from keras.models import Model
from keras.models import load_model
from numpy import argmax
import cv2
import matplotlib.pyplot as plt
from keras.layers import Bidirectional
import cv2
from keras import optimizers
import networkx as nx
import sys
from datetime import datetime
import pandas as pd
import plotly.express as px
import time
import numpy as np
from PIL import Image as pil_image
from keras.preprocessing.image import save_img
from keras import layers
from keras.applications import vgg19
from keras import backend as K


# ***Helper Funnctions***

In [21]:
def save_descriptions(descriptions, filename):
	lines = list()
	for key, desc_list in descriptions.items():
		for desc in desc_list[1]:
			lines.append(str(key) + ' ' + desc)
	data = '\n'.join(lines)
	file = open('../Description_Text/'+filename, 'w')
	file.write(data)
	file.close()

In [22]:
def time_Per_Picture(path):

  video = cv2.VideoCapture(path);
      
  # Find OpenCV version
  (major_ver, minor_ver, subminor_ver) = (cv2.__version__).split('.')
      
  if int(major_ver)  < 3 :
    fps = video.get(cv2.cv.CV_CAP_PROP_FPS)
    print ("Frames per second using video.get(cv2.cv.CV_CAP_PROP_FPS): {0}".format(fps))
  else :
    fps = video.get(cv2.CAP_PROP_FPS)
    print ("Frames per second using video.get(cv2.CAP_PROP_FPS) : {0}".format(fps))
      
  video.release();
  time = 1000/fps 
  print("{0} ms".format(time))
  return time 

# ***Extracting Features from image***

In [11]:
def extract_features(directory):
	# load the model
	model = VGG19()
	# re-structure the model
	model.layers.pop()
	model = Model(inputs=model.inputs, outputs=model.layers[-1].output)
	# summarize
	print(model.summary())
	# extract features from each photo
	features = dict()
	for image_id,image in directory.items():
		# start time
		start = datetime.now()
		image = image[0].resize((224,224), Image.ANTIALIAS)
		print("Size of each pictures after tranformation",sys.getsizeof(image.tobytes()))
		# convert the image pixels to a numpy array
		image = img_to_array(image)
		# reshape data for the model
		image = image.reshape((1, image.shape[0], image.shape[1], image.shape[2]))
		# prepare the image for the VGG model
		image = preprocess_input(image)
		# get features
		feature = model.predict(image, verbose=0)
		# store feature
		features[image_id] = feature
		print("Size of each pictures after feature extraction",sys.getsizeof(feature.tobytes()))  
		print('picture number >%s' % image_id)
	 	# stop time
		stop = datetime.now()
 		# time
		print("time - taken : ",stop-start)
	return features

# ***Creating Captions***

In [24]:
time = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
frames = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]

# calculating time per frame
time_per_frame = time_Per_Picture("../Video/Garment.mp4")
# image dict
image_list = {}
# caption list                                                                      
captions = []
# counter   
count = 0          
caption_list = ["denims on shaft","denims on table","marks is checked by worker",
                "denims on forklift and worker holds it","roller on fabric and fabric on table","cutting the fabric","folding the cloth","sheet is rolled and marker is checked",
                  "worker is cutting the fabric with machine","pieces are marked by woker","clothes are strapped by worker","clothes are sown with machine by worker",
                "iron the clothes","trimming and inspection of clothes by workers","removing the seal from denim","spot the clothes for coloring"]                                                                
for filename in glob.glob('../NewImage/*.jpg'):                                        #assuming gif
    img=Image.open(filename)       
    size = sys.getsizeof(img.tobytes())                                               #the take the filename 
    Unique = int(re.sub("\D", "", filename ))                                        #removing all the letters to create unique ID
    print("photo number: {} Size: {}".format(Unique,size))
    if (Unique <1093 and Unique >= 407):
      caption1 = "denims on shaft";
      caption2 = "shaft has denims";
      captions = [caption1,caption2]
      time[0] += time_per_frame
      frames[0] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <1637 and Unique >= 1116):
      caption1 = "denims on table";
      caption2 = "table has denims";
      captions = [caption1,caption2]
      time[1] += time_per_frame
      frames[1] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <1945 and Unique >= 1655):
      caption1 = "marks is checked by worker";
      caption2 = "worker is looking at marks";
      captions = [caption1,caption2]
      time[2] += time_per_frame
      frames[2] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <2493 and Unique >= 1946):
      caption1 = "denims on forklift and worker holds it";
      caption2 = "worker holds denims and denims on forklift";
      captions = [caption1,caption2]
      time[3] += time_per_frame
      frames[3] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <3600 and Unique >= 2494) or (Unique <4490 and Unique >= 3990):
      caption1 = "roller on fabric and fabric on table";
      caption2 = "fabric on table and roller on fabric";
      captions = [caption1,caption2]
      time[4] += time_per_frame
      frames[4] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <3990 and Unique >= 3600) or (Unique <4912 and Unique >=4475) or (Unique <5651 and Unique >=5184):
      caption1 = "cutting the fabric";
      caption2 = "fabric is sliced";
      captions = [caption1,caption2]
      time[5] += time_per_frame
      frames[5] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <5184 and Unique >=4912):
      caption1 = "folding the cloth";
      caption2 = "cloth is folded"; 
      captions = [caption1,caption2]
      time[6] += time_per_frame
      frames[6] +=1
      image_list.update({Unique:[img,captions]}) 
    elif (Unique <6746 and Unique >=5726):
      caption1 = "sheet is rolled and marker is checked";
      caption2 = "marker is checked and sheet is rolled"; 
      captions = [caption1,caption2]
      time[7] += time_per_frame
      frames[7] +=1
      image_list.update({Unique:[img,captions]})     
    elif (Unique <7391 and Unique >=6746) or (Unique <8036 and Unique >=6746):
      caption1 = "worker is cutting the fabric with machine";
      caption2 = "worker is cutting the fabric with machine"; 
      captions = [caption1,caption2]
      time[8] += time_per_frame
      frames[8] +=1
      image_list.update({Unique:[img,captions]})
    elif (Unique <9223 and Unique >=8037):
      caption1 = "pieces are marked by woker";
      caption2 = "mark the pieces for label"; 
      captions = [caption1,caption2]
      time[9] += time_per_frame
      frames[9] +=1  
      image_list.update({Unique:[img,captions]})
    elif (Unique <9767 and Unique >=9224):
      caption1 = "clothes are strapped by worker";
      caption2 = "workers are strapping the clothes"; 
      captions = [caption1,caption2]
      time[10] += time_per_frame
      frames[10] +=1
      image_list.update({Unique:[img,captions]})            
    elif (Unique <12066 and Unique >=10916) or (Unique <15437 and Unique >=10916):
      caption1 = "clothes are sown with machine by worker";
      caption2 = "sowing the clothes with machine by worker"; 
      captions = [caption1,caption2]
      time[11] += time_per_frame
      frames[11] +=1
      image_list.update({Unique:[img,captions]}) 
    elif (Unique <26652 and Unique >= 26331):
      caption1 = "iron the clothes";
      caption2 = "ironning a cloth"; 
      captions = [caption1,caption2]
      time[12] += time_per_frame
      frames[12] +=1
      image_list.update({Unique:[img,captions]}) 
    elif (Unique <36545 and Unique >=36050):
      caption1 = "trimming and inspection of clothes by workers";
      caption2 = "inspection of clothes by workers for trimming"; 
      captions = [caption1,caption2]
      time[13] += time_per_frame
      frames[13] +=1
      image_list.update({Unique:[img,captions]}) 
    elif (Unique <37666  and Unique >=37063):
      caption1 = "removing the seal from denim";
      caption2 = "seal is removed"; 
      captions = [caption1,caption2]
      time[14] += time_per_frame
      frames[14] +=1
      image_list.update({Unique:[img,captions]}) 
    elif (Unique <40400 and Unique >=38468):
      caption1 = "spot the clothes for coloring";
      caption2 = "spot and dot for color"; 
      captions = [caption1,caption2]
      time[15] += time_per_frame
      frames[15] +=1
      image_list.update({Unique:[img,captions]}) 

  



Frames per second using video.get(cv2.CAP_PROP_FPS) : 30.0
33.333333333333336 ms
photo number: 23001 Size: 230433
photo number: 4626 Size: 230433
photo number: 9717 Size: 230433
photo number: 19279 Size: 230433
photo number: 32683 Size: 230433
photo number: 4150 Size: 230433
photo number: 16675 Size: 230433
photo number: 18077 Size: 230433
photo number: 29148 Size: 230433
photo number: 18004 Size: 230433
photo number: 29445 Size: 230433
photo number: 29814 Size: 230433
photo number: 17736 Size: 230433
photo number: 26680 Size: 230433
photo number: 7008 Size: 230433
photo number: 12930 Size: 230433
photo number: 43224 Size: 230433
photo number: 36624 Size: 230433
photo number: 16815 Size: 230433
photo number: 26900 Size: 230433
photo number: 34579 Size: 230433
photo number: 41427 Size: 230433
photo number: 8941 Size: 230433
photo number: 7308 Size: 230433
photo number: 38768 Size: 230433
photo number: 42824 Size: 230433
photo number: 28760 Size: 230433
photo number: 20162 Size: 230433
p

photo number: 13440 Size: 230433
photo number: 26142 Size: 230433
photo number: 15001 Size: 230433
photo number: 26262 Size: 230433
photo number: 310 Size: 230433
photo number: 36023 Size: 230433
photo number: 21613 Size: 230433
photo number: 12159 Size: 230433
photo number: 42497 Size: 230433
photo number: 44494 Size: 230433
photo number: 2456 Size: 230433
photo number: 4273 Size: 230433
photo number: 2059 Size: 230433
photo number: 33511 Size: 230433
photo number: 3435 Size: 230433
photo number: 29470 Size: 230433
photo number: 6900 Size: 230433
photo number: 9112 Size: 230433
photo number: 3457 Size: 230433
photo number: 21766 Size: 230433
photo number: 8314 Size: 230433
photo number: 25102 Size: 230433
photo number: 36920 Size: 230433
photo number: 2579 Size: 230433
photo number: 6589 Size: 230433
photo number: 44591 Size: 230433
photo number: 17415 Size: 230433
photo number: 15048 Size: 230433
photo number: 29570 Size: 230433
photo number: 27083 Size: 230433
photo number: 6497 Siz

photo number: 3861 Size: 230433
photo number: 23246 Size: 230433
photo number: 16890 Size: 230433
photo number: 19879 Size: 230433
photo number: 7222 Size: 230433
photo number: 35531 Size: 230433
photo number: 15315 Size: 230433
photo number: 20131 Size: 230433
photo number: 41730 Size: 230433
photo number: 2170 Size: 230433
photo number: 490 Size: 230433
photo number: 44339 Size: 230433
photo number: 25283 Size: 230433
photo number: 2046 Size: 230433
photo number: 20564 Size: 230433
photo number: 23091 Size: 230433
photo number: 29027 Size: 230433
photo number: 10159 Size: 230433
photo number: 29099 Size: 230433
photo number: 11231 Size: 230433
photo number: 7522 Size: 230433
photo number: 24024 Size: 230433
photo number: 38411 Size: 230433
photo number: 25194 Size: 230433
photo number: 28827 Size: 230433
photo number: 9673 Size: 230433
photo number: 31069 Size: 230433
photo number: 6086 Size: 230433
photo number: 40776 Size: 230433
photo number: 24429 Size: 230433
photo number: 12408

photo number: 32832 Size: 230433
photo number: 9176 Size: 230433
photo number: 1750 Size: 230433
photo number: 7893 Size: 230433
photo number: 5544 Size: 230433
photo number: 3485 Size: 230433
photo number: 42246 Size: 230433
photo number: 43671 Size: 230433
photo number: 23591 Size: 230433
photo number: 73 Size: 230433
photo number: 11296 Size: 230433
photo number: 10422 Size: 230433
photo number: 25989 Size: 230433
photo number: 20956 Size: 230433
photo number: 6990 Size: 230433
photo number: 23925 Size: 230433
photo number: 33402 Size: 230433
photo number: 6460 Size: 230433
photo number: 2445 Size: 230433
photo number: 15010 Size: 230433
photo number: 9637 Size: 230433
photo number: 2634 Size: 230433
photo number: 34342 Size: 230433
photo number: 3316 Size: 230433
photo number: 40602 Size: 230433
photo number: 40376 Size: 230433
photo number: 9415 Size: 230433
photo number: 41360 Size: 230433
photo number: 37541 Size: 230433
photo number: 18766 Size: 230433
photo number: 22845 Size:

photo number: 11331 Size: 230433
photo number: 5568 Size: 230433
photo number: 30286 Size: 230433
photo number: 22774 Size: 230433
photo number: 34042 Size: 230433
photo number: 43553 Size: 230433
photo number: 24236 Size: 230433
photo number: 36179 Size: 230433
photo number: 15537 Size: 230433
photo number: 10056 Size: 230433
photo number: 17627 Size: 230433
photo number: 42464 Size: 230433
photo number: 302 Size: 230433
photo number: 37154 Size: 230433
photo number: 25005 Size: 230433
photo number: 33727 Size: 230433
photo number: 38431 Size: 230433
photo number: 736 Size: 230433
photo number: 38365 Size: 230433
photo number: 33901 Size: 230433
photo number: 36581 Size: 230433
photo number: 17594 Size: 230433
photo number: 26064 Size: 230433
photo number: 966 Size: 230433
photo number: 12854 Size: 230433
photo number: 22967 Size: 230433
photo number: 29559 Size: 230433
photo number: 13258 Size: 230433
photo number: 19738 Size: 230433
photo number: 18874 Size: 230433
photo number: 275

...

photo number: 22092 Size: 230433
photo number: 22509 Size: 230433
photo number: 21760 Size: 230433
photo number: 3175 Size: 230433
photo number: 43393 Size: 230433
photo number: 18181 Size: 230433
photo number: 24265 Size: 230433
photo number: 17159 Size: 230433
photo number: 28189 Size: 230433
photo number: 14503 Size: 230433
photo number: 17952 Size: 230433
photo number: 43049 Size: 230433
photo number: 21362 Size: 230433
photo number: 14532 Size: 230433
photo number: 25571 Size: 230433
photo number: 6950 Size: 230433
photo number: 34745 Size: 230433
photo number: 22567 Size: 230433
photo number: 26798 Size: 230433
photo number: 42364 Size: 230433
photo number: 17973 Size: 230433
photo number: 10218 Size: 230433
photo number: 25781 Size: 230433
photo number: 16392 Size: 230433
photo number: 22914 Size: 230433
photo number: 24010 Size: 230433
photo number: 20528 Size: 230433
photo number: 13666 Size: 230433
photo number: 14420 Size: 230433
photo number: 14177 Size: 230433
photo number

photo number: 35057 Size: 230433
photo number: 7719 Size: 230433
photo number: 1929 Size: 230433
photo number: 11150 Size: 230433
photo number: 15857 Size: 230433
photo number: 42373 Size: 230433
photo number: 6633 Size: 230433
photo number: 12428 Size: 230433
photo number: 23364 Size: 230433
photo number: 19141 Size: 230433
photo number: 7939 Size: 230433
photo number: 22790 Size: 230433
photo number: 27956 Size: 230433
photo number: 39263 Size: 230433
photo number: 44541 Size: 230433
photo number: 28632 Size: 230433
photo number: 16000 Size: 230433
photo number: 39968 Size: 230433
photo number: 26185 Size: 230433
photo number: 16264 Size: 230433
photo number: 29994 Size: 230433
photo number: 30674 Size: 230433
photo number: 16417 Size: 230433
photo number: 15429 Size: 230433
photo number: 27448 Size: 230433
photo number: 37312 Size: 230433
photo number: 42490 Size: 230433
photo number: 16139 Size: 230433
photo number: 16670 Size: 230433
photo number: 27445 Size: 230433
photo number: 

photo number: 11519 Size: 230433
photo number: 34044 Size: 230433
photo number: 21321 Size: 230433
photo number: 11 Size: 230433
photo number: 13866 Size: 230433
photo number: 10407 Size: 230433
photo number: 5619 Size: 230433
photo number: 10745 Size: 230433
photo number: 39005 Size: 230433
photo number: 21691 Size: 230433
photo number: 28467 Size: 230433
photo number: 17571 Size: 230433
photo number: 30008 Size: 230433
photo number: 20277 Size: 230433
photo number: 16964 Size: 230433
photo number: 9828 Size: 230433
photo number: 32826 Size: 230433
photo number: 18570 Size: 230433
photo number: 39904 Size: 230433
photo number: 13919 Size: 230433
photo number: 5549 Size: 230433
photo number: 17339 Size: 230433
photo number: 11421 Size: 230433
photo number: 30551 Size: 230433
photo number: 8738 Size: 230433
photo number: 35097 Size: 230433
photo number: 29672 Size: 230433
photo number: 32456 Size: 230433
photo number: 13944 Size: 230433
photo number: 44135 Size: 230433
photo number: 231

photo number: 39000 Size: 230433
photo number: 15495 Size: 230433
photo number: 41230 Size: 230433
photo number: 43434 Size: 230433
photo number: 43285 Size: 230433
photo number: 18902 Size: 230433
photo number: 4713 Size: 230433
photo number: 3390 Size: 230433
photo number: 32558 Size: 230433
photo number: 10973 Size: 230433
photo number: 4705 Size: 230433
photo number: 37050 Size: 230433
photo number: 39784 Size: 230433
photo number: 27438 Size: 230433
photo number: 6419 Size: 230433
photo number: 39668 Size: 230433
photo number: 36153 Size: 230433
photo number: 23124 Size: 230433
photo number: 14863 Size: 230433
photo number: 39787 Size: 230433
photo number: 38765 Size: 230433
photo number: 39369 Size: 230433
photo number: 9371 Size: 230433
photo number: 1507 Size: 230433
photo number: 16545 Size: 230433
photo number: 16741 Size: 230433
photo number: 1028 Size: 230433
photo number: 44428 Size: 230433
photo number: 40806 Size: 230433
photo number: 16065 Size: 230433
photo number: 753

photo number: 9249 Size: 230433
photo number: 8300 Size: 230433
photo number: 18061 Size: 230433
photo number: 34251 Size: 230433
photo number: 33440 Size: 230433
photo number: 4625 Size: 230433
photo number: 41292 Size: 230433
photo number: 44378 Size: 230433
photo number: 31610 Size: 230433
photo number: 33512 Size: 230433
photo number: 36607 Size: 230433
photo number: 5856 Size: 230433
photo number: 2374 Size: 230433
photo number: 13690 Size: 230433
photo number: 8004 Size: 230433
photo number: 19485 Size: 230433
photo number: 23985 Size: 230433
photo number: 17043 Size: 230433
photo number: 4235 Size: 230433
photo number: 39898 Size: 230433
photo number: 27332 Size: 230433
photo number: 25478 Size: 230433
photo number: 1777 Size: 230433
photo number: 23208 Size: 230433
photo number: 39709 Size: 230433
photo number: 40629 Size: 230433
photo number: 3102 Size: 230433
photo number: 35891 Size: 230433
photo number: 34503 Size: 230433
photo number: 2704 Size: 230433
photo number: 27816 

In [23]:
Work_time_distribution = pd.DataFrame(list(zip(time,caption_list,frames )),columns =['Time','Activity','Frames'])  
Work_time_distribution.to_csv("../video_data_work_time_dist_train.csv", sep='\t', encoding='utf-8')  
fig = px.histogram(Work_time_distribution, x="Activity",y="Time", histfunc='avg')
fig.show()

TypeError: zip argument #1 must support iteration

# ***Extracting feature and description***

"""
We first took the caption from images and captioned them based on the frames, we created caption in two forms one in forward

another in reverse so that 
"""

In [13]:
save_descriptions(image_list,"youtube_video_img2_train.txt")

In [14]:
features = extract_features(image_list)
print('Extracted Features: %d' % len(features))
# save to file
dump(features, open('../Features_pkl/youtube_video_img2_train.pkl', 'wb'))

Instructions for updating:
If using Keras pass *_constraint arguments to layers.

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 224, 224, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 224, 224, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 224, 224, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 112, 112, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 112, 112, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 112, 112, 128)     147584    
___________________________________________

Size of each pictures after feature extraction 16417
picture number >40383
time - taken :  0:00:00.015408
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39292
time - taken :  0:00:00.015925
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >36051
time - taken :  0:00:00.015733
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >40384
time - taken :  0:00:00.015367
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39293
time - taken :  0:00:00.015300
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >37537
time - taken :  0:00:00.015639
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >2

Size of each pictures after feature extraction 16417
picture number >464
time - taken :  0:00:00.015691
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >465
time - taken :  0:00:00.015890
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >466
time - taken :  0:00:00.016005
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >467
time - taken :  0:00:00.015706
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >468
time - taken :  0:00:00.015425
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >469
time - taken :  0:00:00.015320
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >470
time - ta

Size of each pictures after feature extraction 16417
picture number >529
time - taken :  0:00:00.015806
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >530
time - taken :  0:00:00.015709
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >531
time - taken :  0:00:00.015861
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >532
time - taken :  0:00:00.016078
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >533
time - taken :  0:00:00.015936
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >534
time - taken :  0:00:00.015975
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >535
time - ta

Size of each pictures after feature extraction 16417
picture number >596
time - taken :  0:00:00.015685
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >597
time - taken :  0:00:00.015198
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >598
time - taken :  0:00:00.015555
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >599
time - taken :  0:00:00.015707
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >600
time - taken :  0:00:00.015559
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >601
time - taken :  0:00:00.015413
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >602
time - ta

...

Size of each pictures after feature extraction 16417
picture number >7560
time - taken :  0:00:00.015717
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >5073
time - taken :  0:00:00.016354
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39203
time - taken :  0:00:00.016174
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39483
time - taken :  0:00:00.016386
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >37519
time - taken :  0:00:00.016018
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >5075
time - taken :  0:00:00.016091
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >1220

Size of each pictures after feature extraction 16417
picture number >1033
time - taken :  0:00:00.016183
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39487
time - taken :  0:00:00.015796
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >11945
time - taken :  0:00:00.016094
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6317
time - taken :  0:00:00.015799
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39224
time - taken :  0:00:00.016537
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6491
time - taken :  0:00:00.015914
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >1194

Size of each pictures after feature extraction 16417
picture number >40334
time - taken :  0:00:00.016081
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6509
time - taken :  0:00:00.015965
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6510
time - taken :  0:00:00.016280
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39273
time - taken :  0:00:00.016281
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6807
time - taken :  0:00:00.016520
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >40336
time - taken :  0:00:00.015936
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >3924

Size of each pictures after feature extraction 16417
picture number >39263
time - taken :  0:00:00.016306
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >37531
time - taken :  0:00:00.016046
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6325
time - taken :  0:00:00.016160
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39264
time - taken :  0:00:00.016758
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >5383
time - taken :  0:00:00.016684
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6531
time - taken :  0:00:00.016218
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >3926

Size of each pictures after feature extraction 16417
picture number >40370
time - taken :  0:00:00.016417
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >6545
time - taken :  0:00:00.016775
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >39279
time - taken :  0:00:00.016862
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >10919
time - taken :  0:00:00.016117
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >5459
time - taken :  0:00:00.015896
Size of each pictures after tranformation 150561
Size of each pictures after feature extraction 16417
picture number >37194
time - taken :  0:00:00.015996
Extracted Features: 17066
